## (Semantic) Paper 1개 테스트

In [ ]:
import requests
import time

API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

def fetch_paper_data(title, delay=5):
    base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
    headers = {"x-api-key": API_KEY}
    params = {
        "query": title,
        "fields": "title,abstract,authors,venue,citationCount,influentialCitationCount"
    }

    while True:
        try:
            # Send a GET request to the Semantic Scholar API with the API key
            response = requests.get(base_url, params=params, headers=headers)

            # If the request is successful (status code 200)
            if response.status_code == 200:
                data = response.json()
                if 'data' in data and len(data['data']) > 0:
                    paper = data['data'][0]
                    return paper
                else:
                    print("No paper found for title:", title)
                    return None
            elif response.status_code == 429:
                # Too many requests; wait for the specified delay before retrying
                print(f"Rate limit exceeded. Retrying in {delay} seconds...")
                time.sleep(delay)
            else:
                print(f"Error {response.status_code}: {response.text}")
                return None
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}")
            return None

# Example usage
title = "The revised scale for caregiving self-efficacy: reliability and validity studies"
paper_data = fetch_paper_data(title)

if paper_data:
    print("Title:", paper_data.get("title"))
    print("Abstract:", paper_data.get("abstract"))
    print("Authors and Affiliations:")
    for author in paper_data.get("authors", []):
        name = author.get('name')
        affiliation = author.get('affiliations', ['Unknown affiliation'])[0]
        print(f"  {name} - {affiliation}")
    print("Citation Count:", paper_data.get("citationCount"))
    print("Influential Citation Count:", paper_data.get("influentialCitationCount"))
else:
    print("Paper not found or error occurred.")


## (Semantic) Paper 10개 테스트

In [ ]:
import pandas as pd
import requests
import time

API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

def fetch_paper_data(title, delay=5):
    base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
    headers = {"x-api-key": API_KEY}
    params = {
        "query": title,
        "fields": "title,abstract,authors,venue,citationCount,influentialCitationCount"
    }

    while True:
        try:
            response = requests.get(base_url, params=params, headers=headers)

            if response.status_code == 200:
                data = response.json()
                if 'data' in data and len(data['data']) > 0:
                    return data['data'][0]
                else:
                    print("No paper found for title:", title)
                    return None
            elif response.status_code == 429:
                print(f"Rate limit exceeded. Retrying in {delay} seconds...")
                time.sleep(delay)
            else:
                print(f"Error {response.status_code}: {response.text}")
                return None
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}")
            return None

def collect_paper_info(papers):
    paper_list = []

    for title in papers:
        paper_data = fetch_paper_data(title)
        if paper_data:
            authors = "; ".join([f"{author['name']}" 
                                              for author in paper_data.get("authors", [])])
            paper_list.append({
                "Title": paper_data.get("title"),
                "Abstract": paper_data.get("abstract", ""),
                "Authors": authors,
                "Citation Count": paper_data.get("citationCount"),
                "Influential Citation Count": paper_data.get("influentialCitationCount")
            })
        else:
            print(f"No data found for paper: {title}")

    return pd.DataFrame(paper_list)

# Load the CSV file
file_path = 'Collabo_Paper.csv'
df = pd.read_csv(file_path, encoding='utf-8')

# Select the first 10 papers from '논문명'
papers = df['논문명'].head(10)

# Collect the information
new_df = collect_paper_info(papers)

## (Semantic) 전체 Collect (순차적)

In [ ]:
import pandas as pd
import requests
import time

API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

def fetch_paper_data(title, delay=5):
    base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
    headers = {"x-api-key": API_KEY}
    params = {
        "query": title,
        "fields": "title,abstract,authors,venue,citationCount,influentialCitationCount"
    }

    while True:
        try:
            response = requests.get(base_url, params=params, headers=headers)

            if response.status_code == 200:
                data = response.json()
                if 'data' in data and len(data['data']) > 0:
                    return data['data'][0]
                else:
                    return None  # Return None if no paper is found
            elif response.status_code == 429:
                print(f"Rate limit exceeded. Retrying in {delay} seconds...")
                time.sleep(delay)
            else:
                print(f"Error {response.status_code}: {response.text}")
                return None
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}")
            return None

def collect_paper_info(papers):
    paper_list = []
    no_paper_found_count = 0
    no_data_found_count = 0

    for index, title in enumerate(papers):  # Get index along with title
        print(f"Processing paper {index + 1}/{len(papers)}")  # Show current paper index
        paper_data = fetch_paper_data(title)
        if paper_data:
            authors = "; ".join([f"{author['name']}" for author in paper_data.get("authors", [])])
            paper_list.append({
                "Title": paper_data.get("title"),
                "Abstract": paper_data.get("abstract", ""),
                "Authors": authors,
                "Citation Count": paper_data.get("citationCount"),
                "Influential Citation Count": paper_data.get("influentialCitationCount")
            })
        else:
            if title:
                no_paper_found_count += 1
            else:
                no_data_found_count += 1

    # Print counts at the end
    print(f"No paper found for title: {no_paper_found_count} times")
    print(f"No data found for paper: {no_data_found_count} times")

    return pd.DataFrame(paper_list)

# Load the CSV file
file_path = 'Collabo_Paper.csv'
df = pd.read_csv(file_path, encoding='utf-8')

papers = df['논문명']

# Collect the information
new_df = collect_paper_info(papers)

# Save the DataFrame to a CSV file
new_df.to_csv('collected_paper_info.csv', index=False, encoding='utf-8')


## (Semantic) 전체 Collect (병렬)

In [1]:
import pandas as pd
import requests
import time
from concurrent.futures import ThreadPoolExecutor, as_completed

API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

def fetch_paper_data(title):
    base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
    headers = {"x-api-key": API_KEY}
    params = {
        "query": title,
        "fields": "title,abstract,authors,venue,citationCount,influentialCitationCount"
    }
    
    delay = 1  # Initial delay for exponential backoff
    max_retries = 5  # Maximum number of retries
    
    for _ in range(max_retries):
        try:
            response = requests.get(base_url, params=params, headers=headers)
            
            if response.status_code == 200:
                data = response.json()
                if 'data' in data and len(data['data']) > 0:
                    return data['data'][0]
                else:
                    return None  # Return None if no paper is found
            elif response.status_code == 429:  # Rate limit exceeded
                print(f"Rate limit. {delay} sec")
                time.sleep(delay)
                delay = min(delay * 2, 64)  # Exponential backoff (doubles each time, max 64 seconds)
            else:
                print(f"Error {response.status_code}: {response.text}")
                return None
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}")
            return None

    return None  # Return None after max retries

def collect_paper_info_parallel(papers):
    paper_list = []
    no_paper_found_count = 0
    no_data_found_count = 0

    # Using ThreadPoolExecutor for parallel processing, reduce the number of threads to avoid API overload
    with ThreadPoolExecutor(max_workers=10) as executor:  # Reduced to 10 workers for safer API use
        futures = {executor.submit(fetch_paper_data, title): title for title in papers}

        for index, future in enumerate(as_completed(futures), start=1):
            title = futures[future]
            print(f"Processing paper {index}/{len(papers)}")  # Show progress
            try:
                paper_data = future.result()
                if paper_data:
                    authors = "; ".join([f"{author['name']}" for author in paper_data.get("authors", [])])
                    paper_list.append({
                        "Title": paper_data.get("title"),
                        "Abstract": paper_data.get("abstract", ""),
                        "Authors": authors,
                        "Citation Count": paper_data.get("citationCount"),
                        "Influential Citation Count": paper_data.get("influentialCitationCount")
                    })
                else:
                    no_paper_found_count += 1
            except Exception as e:
                print(f"Error processing paper titled '{title}': {e}")
                no_data_found_count += 1

    # Print counts at the end
    print(f"No paper found for title: {no_paper_found_count} times")
    print(f"No data found for paper: {no_data_found_count} times")

    return pd.DataFrame(paper_list)

# Load the CSV file
file_path = 'Collabo_Paper.csv'
df = pd.read_csv(file_path, encoding='utf-8')

papers = df['논문명']

# Collect the information in parallel
new_df = collect_paper_info_parallel(papers)

# Save the DataFrame to a CSV file
new_df.to_csv('Collabo_Paper_Sem.csv', index=False, encoding='utf-8')

Rate limit. 1 sec
Processing paper 1/42231
Processing paper 2/42231
Processing paper 3/42231
Processing paper 4/42231
Processing paper 5/42231
Processing paper 6/42231
Processing paper 7/42231
Processing paper 8/42231
Processing paper 9/42231
Rate limit. 1 sec
Processing paper 10/42231
Processing paper 11/42231
Rate limit. 1 sec
Processing paper 12/42231
Processing paper 13/42231
Processing paper 14/42231
Processing paper 15/42231
Processing paper 16/42231
Processing paper 17/42231
Rate limit. 1 sec
Rate limit. 1 sec
Processing paper 18/42231
Processing paper 19/42231
Processing paper 20/42231
Processing paper 21/42231
Rate limit. 1 sec
Rate limit. 1 sec
Rate limit. 1 sec
Rate limit. 2 sec
Processing paper 22/42231
Processing paper 23/42231
Processing paper 24/42231
Processing paper 25/42231
Processing paper 26/42231
Rate limit. 1 sec
Processing paper 27/42231
Rate limit. 1 sec
Processing paper 28/42231
Processing paper 29/42231
Processing paper 30/42231
Processing paper 31/42231
Rate 

## (Semantic) 누락 데이터 (7천개 수집)

In [4]:
import pandas as pd
import requests
import time

API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

def normalize_title(title):
    """Remove leading/trailing spaces, convert to lowercase, and remove non-alphanumeric characters"""
    return ''.join(e for e in title.lower().strip() if e.isalnum())

def fetch_paper_data(title):
    base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
    headers = {"x-api-key": API_KEY}
    params = {
        "query": title,
        "fields": "title,abstract,authors,venue,citationCount,influentialCitationCount"
    }
    
    delay = 1  # Initial delay for exponential backoff
    max_retries = 5  # Maximum number of retries
    
    for _ in range(max_retries):
        try:
            response = requests.get(base_url, params=params, headers=headers)
            
            if response.status_code == 200:
                data = response.json()
                if 'data' in data and len(data['data']) > 0:
                    return data['data'][0]
                else:
                    return None  # Return None if no paper is found
            elif response.status_code == 429:  # Rate limit exceeded
                print(f"Rate limit exceeded. Retrying in {delay} seconds...")
                time.sleep(delay)
                delay = min(delay * 2, 64)  # Exponential backoff (doubles each time, max 64 seconds)
            else:
                print(f"Error {response.status_code}: {response.text}")
                return None
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}")
            return None

    return None  # Return None after max retries

def collect_paper_info(papers):
    paper_list = []
    no_paper_found_count = 0

    # Collect data sequentially to avoid data loss
    for index, title in enumerate(papers, start=1):
        print(f"Processing paper {index}/{len(papers)}")  # Show progress
        paper_data = fetch_paper_data(title)
        if paper_data:
            authors = "; ".join([f"{author['name']}" for author in paper_data.get("authors", [])])
            paper_list.append({
                "Title": paper_data.get("title"),
                "Abstract": paper_data.get("abstract", ""),
                "Authors": authors,
                "Citation Count": paper_data.get("citationCount"),
                "Influential Citation Count": paper_data.get("influentialCitationCount")
            })
        else:
            no_paper_found_count += 1

    # Print count of papers not found
    print(f"No paper found for title: {no_paper_found_count} times")

    return pd.DataFrame(paper_list)

# Load the original CSV and the already collected data
collabo_paper = pd.read_csv('Collabo_Paper.csv', encoding='utf-8')
collabo_paper_sem = pd.read_csv('Collabo_Paper_Sem.csv', encoding='utf-8')

# Normalize titles in both datasets for reliable comparison
collabo_paper['Normalized_Title'] = collabo_paper['논문명'].apply(normalize_title)
collabo_paper_sem['Normalized_Title'] = collabo_paper_sem['Title'].apply(normalize_title)

# Identify missing papers by comparing normalized titles
missing_papers = collabo_paper[~collabo_paper['Normalized_Title'].isin(collabo_paper_sem['Normalized_Title'])]

# Check how many papers are missing
print(f"Missing papers: {len(missing_papers)}")

# Collect the missing paper data sequentially
missing_papers_titles = missing_papers['논문명']
missing_data = collect_paper_info(missing_papers_titles)

# Append the missing data to the existing data
collabo_paper_sem_updated = pd.concat([collabo_paper_sem, missing_data], ignore_index=True)

# Save the updated data to a CSV file
collabo_paper_sem_updated.to_csv('Collabo_Paper_Sem_Updated.csv', index=False, encoding='utf-8')


Missing papers: 8390
Processing paper 1/8390
Processing paper 2/8390
Processing paper 3/8390
Processing paper 4/8390
Processing paper 5/8390
Processing paper 6/8390
Processing paper 7/8390
Rate limit exceeded. Retrying in 1 seconds...
Processing paper 8/8390
Processing paper 9/8390
Processing paper 10/8390
Rate limit exceeded. Retrying in 1 seconds...
Processing paper 11/8390
Processing paper 12/8390
Rate limit exceeded. Retrying in 1 seconds...
Rate limit exceeded. Retrying in 2 seconds...
Processing paper 13/8390
Processing paper 14/8390
Processing paper 15/8390
Processing paper 16/8390
Processing paper 17/8390
Processing paper 18/8390
Processing paper 19/8390
Processing paper 20/8390
Processing paper 21/8390
Processing paper 22/8390
Processing paper 23/8390
Processing paper 24/8390
Processing paper 25/8390
Processing paper 26/8390
Processing paper 27/8390
Processing paper 28/8390
Processing paper 29/8390
Processing paper 30/8390
Processing paper 31/8390
Rate limit exceeded. Retrying

## (Semantic) 디코딩 해결

In [ ]:
# ?륹 = -W
# ?륢 = -G
# ?릈 = -H
# ?릂 = -E
# ?륣 = -H
# ?륲 = -S
# ?륝 = -C
# ?륥 = -J
# ?릋 = -I
# ?릃 = -F
# ?륯 = -P
# ?륤 = -I
# ?륶 = -U
# ?륪 = -M
# ?릀 = -C
# ?릌 = -J
# ?륳 = -T
# ?릝 = -Y
# ?륦 = -K
# ?뭆 = -S
# ?륞 = -D
# ?륻 = -Y
# ?뭯 = -X
# ?릗 = -S
# ?섲 = 'A
# ?륮 = -O
# ?륿 = -B
# ?릛 = -W
# ?릖 = -R

# 竊? = ""
# 훻 = Č
# 훾 = c
# 훶 = ć
# 킁 = ů
# 탑 = ž
# 찼 = a
# 처 = o
# 흢 = ł
# 횋 = E
# 큄 = s
# 챰 = ñ
# 훱 = a
# 힄 = ś
# 흦 = ń

# ?? = '

## (Semantic) Affiliation 3차 시도

In [7]:
# import pandas as pd
# import requests
# import time

# API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

# def fetch_paper_data(title, delay=5):
#     base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
#     headers = {"x-api-key": API_KEY}
#     params = {
#         "query": title,
#         "fields": "title,abstract,authors,venue,citationCount,influentialCitationCount"
#     }

#     while True:
#         try:
#             response = requests.get(base_url, params=params, headers=headers)

#             if response.status_code == 200:
#                 data = response.json()
#                 if 'data' in data and len(data['data']) > 0:
#                     return data['data'][0]
#                 else:
#                     return None  # Return None if no paper is found
#             elif response.status_code == 429:
#                 time.sleep(delay)
#             else:
#                 print(f"Error {response.status_code}: {response.text}")
#                 return None
#         except requests.exceptions.RequestException as e:
#             print(f"Request failed: {e}")
#             return None

# def collect_paper_info(papers):
#     paper_list = []
#     no_paper_found_count = 0
#     no_data_found_count = 0

#     for index, row in papers.iterrows():  # Iterate through the filtered DataFrame
#         title = row['Title']  # Access the title from the row
#         authors = row['Authors']  # Access the authors from the row
#         paper_data = fetch_paper_data(title)
        
#         # Check if both conditions are satisfied
#         if paper_data and (pd.isna(authors) or authors == ""):  # Check if authors is NaN or empty
#             authors = "; ".join([f"{author['name']}" for author in paper_data.get("authors", [])])
#             paper_list.append({
#                 "Title": paper_data.get("title"),
#                 "Abstract": paper_data.get("abstract", ""),
#                 "Authors": authors,
#                 "Citation Count": paper_data.get("citationCount"),
#                 "Influential Citation Count": paper_data.get("influentialCitationCount")
#             })
#         else:
#             if title:
#                 no_paper_found_count += 1
#             else:
#                 no_data_found_count += 1

#     # Print counts at the end
#     print(f"No paper found for title: {no_paper_found_count} times")
#     print(f"No data found for paper: {no_data_found_count} times")

#     return pd.DataFrame(paper_list)

# # Load the CSV file
# file_path = 'Paper_Dataset_Test.csv' 
# df = pd.read_csv(file_path, encoding='utf-8')

# # Filter the DataFrame for the specific conditions
# filtered_df = df[(df['육T관련기술'] == 2) & (df['Authors'].isnull() | (df['Authors'] == ''))]

# # Collect the information
# new_df = collect_paper_info(filtered_df[['ID','Title', 'Authors']])

# # Save the DataFrame to a CSV file
# new_df.to_csv('Paper_Dataset_Test_2.csv', index=False, encoding='utf-8')


C:\Users\river\AppData\Local\Temp\ipykernel_14708\57110786.py:68: DtypeWarning: Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path, encoding='utf-8')


No paper found for title: 55 times
No data found for paper: 0 times


In [15]:
# ID 추가

import pandas as pd
import requests
import time

API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

def fetch_paper_data(title, delay=5):
    base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
    headers = {"x-api-key": API_KEY}
    params = {
        "query": title,
        "fields": "title,abstract,authors,venue,citationCount,influentialCitationCount"
    }

    while True:
        try:
            response = requests.get(base_url, params=params, headers=headers)

            if response.status_code == 200:
                data = response.json()
                if 'data' in data and len(data['data']) > 0:
                    return data['data'][0]
                else:
                    return None  # Return None if no paper is found
            elif response.status_code == 429:
                time.sleep(delay)
            else:
                print(f"Error {response.status_code}: {response.text}")
                return None
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}")
            return None

def collect_paper_info(papers):
    paper_list = []
    no_paper_found_count = 0
    no_data_found_count = 0

    for index, row in papers.iterrows():  # Iterate through the filtered DataFrame
        title = row['Title']  # Access the title from the row
        authors = row['Authors']  # Access the authors from the row
        paper_data = fetch_paper_data(title)

        # Check if both conditions are satisfied
        if paper_data and (pd.isna(authors) or authors == ""):  # Check if authors is NaN or empty
            authors = "; ".join([f"{author['name']}" for author in paper_data.get("authors", [])])
            paper_list.append({
                "ID": row['ID'],  # Include the ID from the original DataFrame
                "Title": paper_data.get("title"),
                "Abstract": paper_data.get("abstract", ""),
                "Authors": authors,
                "Citation Count": paper_data.get("citationCount"),
                "Influential Citation Count": paper_data.get("influentialCitationCount")
            })
        else:
            if title:
                no_paper_found_count += 1
            else:
                no_data_found_count += 1

    # Print counts at the end
    print(f"No paper found for title: {no_paper_found_count} times")
    print(f"No data found for paper: {no_data_found_count} times")

    return pd.DataFrame(paper_list)

# Load the CSV file
file_path = 'Paper_Dataset.csv' 
df = pd.read_csv(file_path, encoding='utf-8-sig')

# Filter the DataFrame for the specific conditions
filtered_df = df[(df['육T관련기술'] == 2) & (df['Authors'].isnull() | (df['Authors'] == ''))]

# Collect the information
new_df = collect_paper_info(filtered_df[['ID', 'Title', 'Authors']])  # Include 'ID' in the selected columns

# Save the DataFrame to a CSV file
new_df.to_csv('Paper_Dataset_Missing_SEM.csv', index=False, encoding='utf-8-sig')


C:\Users\river\AppData\Local\Temp\ipykernel_14708\2906268627.py:71: DtypeWarning: Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path, encoding='utf-8-sig')


No paper found for title: 55 times
No data found for paper: 0 times


In [8]:
# Save the DataFrame to a CSV file
new_df.to_csv('Paper_Dataset_Test_3.csv', index=False, encoding='utf-8-sig')

In [14]:
import pandas as pd

# Load the original dataset and the new dataset
paper_dataset_path = 'Paper_Dataset.csv'
new_df_path = 'Paper_Dataset_Missing_SEM.csv'

# Load the datasets
paper_df = pd.read_csv(paper_dataset_path, encoding='utf-8')
new_df = pd.read_csv(new_df_path, encoding='utf-8')

# Update the relevant columns in paper_df with values from new_df where IDs match
for index, new_row in new_df.iterrows():
    id_value = new_row['ID']  # Get the ID from new_df
    
    # Check if the ID exists in paper_df
    if id_value in paper_df['ID'].values:
        paper_df.loc[paper_df['ID'] == id_value, ['Authors', 'Abstract', 'Citation Count', 'Influential Citation Count']] = (
            new_row['Authors'], 
            new_row['Abstract'], 
            new_row['Citation Count'], 
            new_row['Influential Citation Count']
        )

# Save the updated DataFrame to a new CSV file
paper_df.to_csv('Paper_Dataset_2.csv', index=False, encoding='utf-8-sig')


C:\Users\river\AppData\Local\Temp\ipykernel_14708\3657947889.py:8: DtypeWarning: Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.
  paper_df = pd.read_csv(paper_dataset_path, encoding='utf-8')


## (Elsevier) Affiliation만 가져오기 - Test

In [2]:
import requests
import json

# Define the API key and base URL for the Elsevier Scopus API
api_key = 'c27cd191092b7de4f2b050c6cd66e8d9'  # Replace with your API key
base_url = 'https://api.elsevier.com/content/search/scopus'

# Define the paper title you want to search
paper_title = 'Direct Determination of Gold in Rock Samples Using Collision Cell Quadrupole ICP-MS'

# Define the API parameters for the request
params = {
    'query': f'TITLE("{paper_title}")',
    'apiKey': api_key,
    'field': 'dc:title,author,affiliation,dc:description',
    'count': 1  # Retrieve only 1 result (adjust if needed)
}

# Send the GET request to the Elsevier API
response = requests.get(base_url, headers={'Accept': 'application/json'}, params=params)

# Check if the request was successful
if response.status_code == 200:
    # Parse the response as JSON
    data = response.json()
    
    # Extract the first entry from the search results
    if 'search-results' in data and 'entry' in data['search-results']:
        entry = data['search-results']['entry'][0]
        
        # Extract the relevant fields from the response
        title = entry.get('dc:title', 'No Title Found')
        abstract = entry.get('dc:description', 'No Abstract Found')
        authors = entry.get('author', [])
        affiliations = entry.get('affiliation', [])
        
        # Collect authors' names
        author_list = [author.get('authname', 'No Author Name') for author in authors]
        
        # Collect affiliation names
        affiliation_list = [affiliation.get('affilname', 'No Affiliation Name') for affiliation in affiliations]
        
        # Display the collected data
        print("Title:", title)
        print("Authors:", author_list)
        print("Affiliations:", affiliation_list)
        print("Abstract:", abstract)
    
    else:
        print("No search results found for the given title.")
else:
    print(f"Failed to retrieve data. HTTP Status Code: {response.status_code}")


Title: Direct determination of gold in rock samples using collision cell quadrupole ICP-MS
Authors: []
Affiliations: ['Korea Institute of Nuclear Safety', 'Chungnam National University']
Abstract: No Abstract Found


In [3]:
import requests
import json

# Define the API key and base URL for the Elsevier Scopus API
api_key = 'c27cd191092b7de4f2b050c6cd66e8d9'  # Replace with your API key
base_url = 'https://api.elsevier.com/content/search/scopus'

# Define the paper title you want to search
paper_title = 'Direct Determination of Gold in Rock Samples Using Collision Cell Quadrupole ICP-MS'

# Define the API parameters for the request
params = {
    'query': f'TITLE("{paper_title}")',
    'apiKey': api_key,
    'field': 'dc:title,dc:creator,author,affiliation,dc:description',  # Added dc:creator for author names
    'count': 1  # Retrieve only 1 result (adjust if needed)
}

# Send the GET request to the Elsevier API
response = requests.get(base_url, headers={'Accept': 'application/json'}, params=params)

# Check if the request was successful
if response.status_code == 200:
    # Parse the response as JSON
    data = response.json()
    
    # Extract the first entry from the search results
    if 'search-results' in data and 'entry' in data['search-results']:
        entry = data['search-results']['entry'][0]
        
        # Extract the relevant fields from the response
        title = entry.get('dc:title', 'No Title Found')
        abstract = entry.get('dc:description', 'No Abstract Found')
        
        # Get authors' names from dc:creator field
        authors = entry.get('dc:creator', 'No Authors Found')
        
        # If author data is in a different format, we try the 'author' field
        if authors == 'No Authors Found':
            authors = [author.get('authname', 'No Author Name') for author in entry.get('author', [])]
        
        # Collect affiliation names
        affiliations = [affiliation.get('affilname', 'No Affiliation Name') for affiliation in entry.get('affiliation', [])]
        
        # Display the collected data
        print("Title:", title)
        print("Authors:", authors)
        print("Affiliations:", affiliations)
        print("Abstract:", abstract)
    
    else:
        print("No search results found for the given title.")
else:
    print(f"Failed to retrieve data. HTTP Status Code: {response.status_code}")


Title: Direct determination of gold in rock samples using collision cell quadrupole ICP-MS
Authors: Yim S.A.
Affiliations: ['Korea Institute of Nuclear Safety', 'Chungnam National University']
Abstract: No Abstract Found


## (Elsevier) 전체 Collect (1 Api = 19000여개)

In [ ]:
import requests
import pandas as pd

# Define the API key and base URL for the Elsevier Scopus API
api_key = 'af0b42c9935cd05e317192d37199ca43'  # Replace with your API key
base_url = 'https://api.elsevier.com/content/search/scopus'

# Function to retrieve affiliation data using the Scopus API
def get_affiliations(paper_title):
    params = {
        'query': f'TITLE("{paper_title}")',
        'apiKey': api_key,
        'field': 'affiliation',  # Retrieve only affiliation info
        'count': 1  # Retrieve only 1 result (adjust if needed)
    }
    
    response = requests.get(base_url, headers={'Accept': 'application/json'}, params=params)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        
        # Extract the first entry from the search results
        if 'search-results' in data and 'entry' in data['search-results']:
            entry = data['search-results']['entry'][0]
            
            # Collect affiliation names
            affiliations = [affiliation.get('affilname', 'No Affiliation Name') for affiliation in entry.get('affiliation', [])]
            
            # Join affiliations with semicolons
            return '; '.join(affiliations)
        else:
            return 'No Affiliations Found'
    else:
        return f"API Error: {response.status_code}"

# Read the Collabo_Paper.csv file
file_path = 'Collabo_Paper.csv'
df = pd.read_csv(file_path, encoding='utf-8')

# Create a new DataFrame to store titles and affiliations
results = pd.DataFrame(columns=['Title', 'Affiliation'])

# Loop through each paper title in the full DataFrame
total_papers = len(df)
for index, paper in enumerate(df['논문명']):
    # Print the progress message
    print(f"Processing paper {index + 1}/{total_papers}")
    
    # Get affiliation data for each paper title
    affiliations = get_affiliations(paper)
    
    # Create a new DataFrame row with the title and affiliations
    new_row = pd.DataFrame({'Title': [paper], 'Affiliation': [affiliations]})
    
    # Concatenate the new row to the results DataFrame
    results = pd.concat([results, new_row], ignore_index=True)

# Save the resulting DataFrame to a new CSV file
results.to_csv('Collabo_Paper_Elsevier.csv', index=False, encoding='utf-8')

print("Affiliation data for 10 papers collected and saved successfully.")


Processing paper 1/42231
Processing paper 2/42231
Processing paper 3/42231
Processing paper 4/42231
Processing paper 5/42231
Processing paper 6/42231
Processing paper 7/42231
Processing paper 8/42231
Processing paper 9/42231
Processing paper 10/42231
Processing paper 11/42231
Processing paper 12/42231
Processing paper 13/42231
Processing paper 14/42231
Processing paper 15/42231
Processing paper 16/42231
Processing paper 17/42231
Processing paper 18/42231
Processing paper 19/42231
Processing paper 20/42231
Processing paper 21/42231
Processing paper 22/42231
Processing paper 23/42231
Processing paper 24/42231
Processing paper 25/42231
Processing paper 26/42231
Processing paper 27/42231
Processing paper 28/42231
Processing paper 29/42231
Processing paper 30/42231
Processing paper 31/42231
Processing paper 32/42231
Processing paper 33/42231
Processing paper 34/42231
Processing paper 35/42231
Processing paper 36/42231
Processing paper 37/42231
Processing paper 38/42231
Processing paper 39/4

## (Elsevier) 누락 데이터 수집 (19000~)

In [2]:
import requests
import pandas as pd
import time

# Define the API key and base URL for the Elsevier Scopus API
api_key = 'd8efd34f0c99887b9c324ca81912fcf3'
base_url = 'https://api.elsevier.com/content/search/scopus'

# Function to retrieve affiliation data using the Scopus API
def get_affiliations(paper_title):
    params = {
        'query': f'TITLE("{paper_title}")',
        'apiKey': api_key,
        'field': 'affiliation',  # Retrieve only affiliation info
        'count': 1  # Retrieve only 1 result (adjust if needed)
    }
    
    response = requests.get(base_url, headers={'Accept': 'application/json'}, params=params)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        
        # Extract the first entry from the search results
        if 'search-results' in data and 'entry' in data['search-results']:
            entry = data['search-results']['entry'][0]
            
            # Collect affiliation names
            affiliations = [affiliation.get('affilname', 'No Affiliation Name') for affiliation in entry.get('affiliation', [])]
            
            # Join affiliations with semicolons
            return '; '.join(affiliations)
        else:
            return 'No Affiliations Found'
    else:
        return f"API Error: {response.status_code}"

# Read the current dataset
file_path = 'Collabo_Paper.csv'
df = pd.read_csv(file_path, encoding='utf-8')

# Create a new DataFrame to store titles and affiliations
results = pd.DataFrame(columns=['Title', 'Affiliation'])

# Load the previous CSV if needed (optional)
try:
    results = pd.read_csv('Collabo_Paper_Elsevier_2.csv', encoding='utf-8')
    print("Loaded previous progress from Collabo_Paper_Elsevier_2.csv")
except FileNotFoundError:
    print("No previous progress found, starting fresh.")

# Define the starting point (19959th paper)
start_paper = 20001

# Loop through each paper title starting from the 19959th entry
total_papers = len(df)

batch_size = 1000

for index, paper in enumerate(df['논문명'][start_paper-1:], start=start_paper):
    print(f"Processing paper {index}/{total_papers}")
    
    # Get affiliation data for each paper title
    affiliations = get_affiliations(paper)
    
    # Handle API rate limit error (429)
    if "API Error: 429" in affiliations:
        print(f"Rate limit reached. Waiting 60 seconds before retrying...")
        time.sleep(60)
        affiliations = get_affiliations(paper)
    
    # Handle other API errors
    if "API Error" in affiliations:
        print(f"Error encountered: {affiliations}. Skipping paper {index}.")
        continue

    # Create a new row and append it to the results DataFrame
    new_row = pd.DataFrame({'Title': [paper], 'Affiliation': [affiliations]})
    results = pd.concat([results, new_row], ignore_index=True)
    
    # Save every 'batch_size' papers
    if index % batch_size == 0:
        results.to_csv('Collabo_Paper_Elsevier_2.csv', index=False, encoding='utf-8')
        print(f"Saved batch of {batch_size} papers. Current index: {index}")

# Save any remaining data after the loop
results.to_csv('Collabo_Paper_Elsevier_2.csv', index=False, encoding='utf-8')

print("Affiliation data collection completed successfully.")


No previous progress found, starting fresh.
Processing paper 20001/42231
Processing paper 20002/42231
Processing paper 20003/42231
Processing paper 20004/42231
Processing paper 20005/42231
Processing paper 20006/42231
Processing paper 20007/42231
Processing paper 20008/42231
Processing paper 20009/42231
Processing paper 20010/42231
Processing paper 20011/42231
Processing paper 20012/42231
Processing paper 20013/42231
Processing paper 20014/42231
Processing paper 20015/42231
Processing paper 20016/42231
Processing paper 20017/42231
Processing paper 20018/42231
Processing paper 20019/42231
Processing paper 20020/42231
Processing paper 20021/42231
Processing paper 20022/42231
Processing paper 20023/42231
Processing paper 20024/42231
Processing paper 20025/42231
Processing paper 20026/42231
Processing paper 20027/42231
Processing paper 20028/42231
Processing paper 20029/42231
Processing paper 20030/42231
Processing paper 20031/42231
Processing paper 20032/42231
Processing paper 20033/42231

KeyboardInterrupt: 

In [5]:
import requests
import pandas as pd
import time

# Define the API key and base URL for the Elsevier Scopus API
api_key = '956707ea4f951462fbc0623544e14440'
base_url = 'https://api.elsevier.com/content/search/scopus'

# Function to retrieve affiliation data using the Scopus API
def get_affiliations(paper_title):
    params = {
        'query': f'TITLE("{paper_title}")',
        'apiKey': api_key,
        'field': 'affiliation',  # Retrieve only affiliation info
        'count': 1  # Retrieve only 1 result (adjust if needed)
    }
    
    response = requests.get(base_url, headers={'Accept': 'application/json'}, params=params)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        
        # Extract the first entry from the search results
        if 'search-results' in data and 'entry' in data['search-results']:
            entry = data['search-results']['entry'][0]
            
            # Collect affiliation names
            affiliations = [affiliation.get('affilname', 'No Affiliation Name') for affiliation in entry.get('affiliation', [])]
            
            # Join affiliations with semicolons
            return '; '.join(affiliations)
        else:
            return 'No Affiliations Found'
    else:
        return f"API Error: {response.status_code}"

# Read the current dataset
file_path = 'Collabo_Paper.csv'
df = pd.read_csv(file_path, encoding='utf-8')

# Create a new DataFrame to store titles and affiliations
results = pd.DataFrame(columns=['Title', 'Affiliation'])

# Load the previous CSV if needed (optional)
try:
    results = pd.read_csv('Collabo_Paper_Elsevier_3.csv', encoding='utf-8')
    print("Loaded previous progress from Collabo_Paper_Elsevier_3.csv")
except FileNotFoundError:
    print("No previous progress found, starting fresh.")

# Define the starting point (19959th paper)
start_paper = 39993

# Loop through each paper title starting from the 19959th entry
total_papers = len(df)

batch_size = 1000

for index, paper in enumerate(df['논문명'][start_paper-1:], start=start_paper):
    print(f"Processing paper {index}/{total_papers}")
    
    # Get affiliation data for each paper title
    affiliations = get_affiliations(paper)
    
    # Handle API rate limit error (429)
    if "API Error: 429" in affiliations:
        print(f"Rate limit reached. Waiting 60 seconds before retrying...")
        time.sleep(60)
        affiliations = get_affiliations(paper)
    
    # Handle other API errors
    if "API Error" in affiliations:
        print(f"Error encountered: {affiliations}. Skipping paper {index}.")
        continue

    # Create a new row and append it to the results DataFrame
    new_row = pd.DataFrame({'Title': [paper], 'Affiliation': [affiliations]})
    results = pd.concat([results, new_row], ignore_index=True)
    
    # Save every 'batch_size' papers
    if index % batch_size == 0:
        results.to_csv('Collabo_Paper_Elsevier_3.csv', index=False, encoding='utf-8')
        print(f"Saved batch of {batch_size} papers. Current index: {index}")

# Save any remaining data after the loop
results.to_csv('Collabo_Paper_Elsevier_3.csv', index=False, encoding='utf-8')

print("Affiliation data collection completed successfully.")


No previous progress found, starting fresh.
Processing paper 39993/42231
Processing paper 39994/42231
Processing paper 39995/42231
Processing paper 39996/42231
Processing paper 39997/42231
Processing paper 39998/42231
Processing paper 39999/42231
Processing paper 40000/42231
Saved batch of 1000 papers. Current index: 40000
Processing paper 40001/42231
Processing paper 40002/42231
Processing paper 40003/42231
Processing paper 40004/42231
Processing paper 40005/42231
Processing paper 40006/42231
Processing paper 40007/42231
Processing paper 40008/42231
Processing paper 40009/42231
Processing paper 40010/42231
Processing paper 40011/42231
Processing paper 40012/42231
Processing paper 40013/42231
Processing paper 40014/42231
Processing paper 40015/42231
Processing paper 40016/42231
Processing paper 40017/42231
Processing paper 40018/42231
Processing paper 40019/42231
Processing paper 40020/42231
Processing paper 40021/42231
Processing paper 40022/42231
Processing paper 40023/42231
Processi

In [7]:
import requests
import pandas as pd

# Define the API key and base URL for the Elsevier Scopus API
api_key = 'c5dab187fadac5ef7df6122571a5c229'  # Replace with your API key
base_url = 'https://api.elsevier.com/content/search/scopus'

# Function to retrieve affiliation data using the Scopus API
def get_affiliations(paper_title):
    params = {
        'query': f'TITLE("{paper_title}")',
        'apiKey': api_key,
        'field': 'affiliation',  # Retrieve only affiliation info
        'count': 1  # Retrieve only 1 result (adjust if needed)
    }
    
    response = requests.get(base_url, headers={'Accept': 'application/json'}, params=params)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        
        # Extract the first entry from the search results
        if 'search-results' in data and 'entry' in data['search-results']:
            entry = data['search-results']['entry'][0]
            
            # Collect affiliation names
            affiliations = [affiliation.get('affilname', 'No Affiliation Name') for affiliation in entry.get('affiliation', [])]
            
            # Join affiliations with semicolons
            return '; '.join(affiliations)
        else:
            return 'No Affiliations Found'
    else:
        return f"API Error: {response.status_code}"

# Read the Paper_Dataset.csv file
file_path = 'Paper_Dataset_2.csv'
df = pd.read_csv(file_path, encoding='utf-8')

# Filter the DataFrame for the specific conditions
filtered_df = df[(df['육T관련기술'] == 2) & (df['Affiliation'].isnull() | (df['Affiliation'] == ''))]

# Create a new DataFrame to store IDs, titles, and affiliations
results = pd.DataFrame(columns=['ID', 'Title', 'Affiliation'])

# Loop through each filtered paper title
total_papers = len(filtered_df)
for index, row in filtered_df.iterrows():
    # Print the progress message
    print(f"Processing paper {index + 1}/{total_papers}")
    
    # Get affiliation data for each paper title
    paper_title = row['Title']
    affiliations = get_affiliations(paper_title)
    
    # Create a new DataFrame row with ID, title, and affiliations
    new_row = pd.DataFrame({
        'ID': [row['ID']],
        'Title': [paper_title],
        'Affiliation': [affiliations]
    })
    
    # Concatenate the new row to the results DataFrame
    results = pd.concat([results, new_row], ignore_index=True)

# Save the resulting DataFrame to a new CSV file
results.to_csv('Paper_Dataset_Missing_ELS.csv', index=False, encoding='utf-8')

print("Affiliation data collected and saved successfully.")


C:\Users\river\AppData\Local\Temp\ipykernel_13896\463019974.py:39: DtypeWarning: Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path, encoding='utf-8')


Processing paper 337/274
Processing paper 395/274
Processing paper 922/274
Processing paper 1068/274
Processing paper 1561/274
Processing paper 1639/274
Processing paper 1695/274
Processing paper 1774/274
Processing paper 2378/274
Processing paper 2404/274
Processing paper 2635/274
Processing paper 2913/274
Processing paper 2915/274
Processing paper 3057/274
Processing paper 3076/274
Processing paper 3119/274
Processing paper 3960/274
Processing paper 3971/274
Processing paper 3973/274
Processing paper 3974/274
Processing paper 4069/274
Processing paper 4406/274
Processing paper 4427/274
Processing paper 4621/274
Processing paper 5169/274
Processing paper 6334/274
Processing paper 6335/274
Processing paper 7024/274
Processing paper 8209/274
Processing paper 8250/274
Processing paper 8349/274
Processing paper 8661/274
Processing paper 8752/274
Processing paper 8838/274
Processing paper 8861/274
Processing paper 9277/274
Processing paper 9723/274
Processing paper 9749/274
Processing pape

In [6]:
import pandas as pd

# Load the original dataset and the new dataset
paper_dataset_path = 'Paper_Dataset.csv'
new_df_path = 'Paper_Dataset_Missing_ELS.csv'

# Load the datasets
paper_df = pd.read_csv(paper_dataset_path, encoding='utf-8')
new_df = pd.read_csv(new_df_path, encoding='utf-8')

# Update only the 'Affiliations' column in paper_df with values from new_df where IDs match
for index, new_row in new_df.iterrows():
    id_value = new_row['ID']  # Get the ID from new_df
    
    # Check if the ID exists in paper_df
    if id_value in paper_df['ID'].values:
        # Update only the 'Affiliations' column
        paper_df.loc[paper_df['ID'] == id_value, 'Affiliation'] = new_row['Affiliation']

# Save the updated DataFrame to a new CSV file
paper_df.to_csv('Paper_Dataset_2.csv', index=False, encoding='utf-8-sig')

print("Affiliation updates based on matching IDs have been saved successfully.")


C:\Users\river\AppData\Local\Temp\ipykernel_13896\2993842799.py:8: DtypeWarning: Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.
  paper_df = pd.read_csv(paper_dataset_path, encoding='utf-8')


Affiliation updates based on matching IDs have been saved successfully.


## 6천개 다시

In [2]:
import requests
import pandas as pd

# Define the API key and base URL for the Elsevier Scopus API
api_key = 'af0b42c9935cd05e317192d37199ca43'  # Replace with your API key
base_url = 'https://api.elsevier.com/content/search/scopus'

# Function to retrieve affiliation data using the Scopus API
def get_affiliations(paper_title):
    params = {
        'query': f'TITLE("{paper_title}")',
        'apiKey': api_key,
        'field': 'affiliation',  # Retrieve only affiliation info
        'count': 1  # Retrieve only 1 result (adjust if needed)
    }
    
    response = requests.get(base_url, headers={'Accept': 'application/json'}, params=params)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        
        # Extract the first entry from the search results
        if 'search-results' in data and 'entry' in data['search-results']:
            entry = data['search-results']['entry'][0]
            
            # Collect affiliation names
            affiliations = [affiliation.get('affilname', 'No Affiliation Name') for affiliation in entry.get('affiliation', [])]
            
            # Join affiliations with semicolons
            return '; '.join(affiliations)
        else:
            return 'No Affiliations Found'
    else:
        return f"API Error: {response.status_code}"

# Read the Collabo_Paper.csv file
file_path = 'matching_raw.csv'
df = pd.read_csv(file_path, encoding='utf-8-sig')

# Create a new DataFrame to store titles and affiliations
results = pd.DataFrame(columns=['Title', 'Affiliation_New'])

# Loop through each paper title in the full DataFrame
total_papers = len(df)
for index, paper in enumerate(df['Title']):
    # Print the progress message
    print(f"Processing paper {index + 1}/{total_papers}")
    
    # Get affiliation data for each paper title
    affiliations = get_affiliations(paper)
    
    # Create a new DataFrame row with the title and affiliations
    new_row = pd.DataFrame({'Title': [paper], 'Affiliation_New': [affiliations]})
    
    # Concatenate the new row to the results DataFrame
    results = pd.concat([results, new_row], ignore_index=True)

# Save the resulting DataFrame to a new CSV file
results.to_csv('matching_raw_new.csv', index=False, encoding='utf-8-sig')


Processing paper 1/6500
Processing paper 2/6500
Processing paper 3/6500
Processing paper 4/6500
Processing paper 5/6500
Processing paper 6/6500
Processing paper 7/6500
Processing paper 8/6500
Processing paper 9/6500
Processing paper 10/6500
Processing paper 11/6500
Processing paper 12/6500
Processing paper 13/6500
Processing paper 14/6500
Processing paper 15/6500
Processing paper 16/6500
Processing paper 17/6500
Processing paper 18/6500
Processing paper 19/6500
Processing paper 20/6500
Processing paper 21/6500
Processing paper 22/6500
Processing paper 23/6500
Processing paper 24/6500
Processing paper 25/6500
Processing paper 26/6500
Processing paper 27/6500
Processing paper 28/6500
Processing paper 29/6500
Processing paper 30/6500
Processing paper 31/6500
Processing paper 32/6500
Processing paper 33/6500
Processing paper 34/6500
Processing paper 35/6500
Processing paper 36/6500
Processing paper 37/6500
Processing paper 38/6500
Processing paper 39/6500
Processing paper 40/6500
Processin

#### Citation 누락

In [19]:
import pandas as pd
import requests
import time

API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"  # Your Semantic Scholar API Key

def fetch_paper_citations(title, delay=5):
    base_url = "https://api.semanticscholar.org/graph/v1/paper/search"
    headers = {"x-api-key": API_KEY}
    params = {
        "query": title,
        "fields": "citationCount,influentialCitationCount"
    }

    while True:
        try:
            response = requests.get(base_url, params=params, headers=headers)

            if response.status_code == 200:
                data = response.json()
                if 'data' in data and len(data['data']) > 0:
                    return {
                        "Citation_Count": data['data'][0].get("citationCount"),
                        "Influential_Citation_Count": data['data'][0].get("influentialCitationCount")
                    }
                else:
                    return {"Citation_Count": None, "Influential_Citation_Count": None}  # No paper found
            elif response.status_code == 429:
                print(f"Rate limit exceeded. Retrying in {delay} seconds...")
                time.sleep(delay)
            else:
                print(f"Error {response.status_code}: {response.text}")
                return {"Citation_Count": None, "Influential_Citation_Count": None}
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}")
            return {"Citation_Count": None, "Influential_Citation_Count": None}

def update_citation_data(filtered_df):
    updated_rows = []
    no_paper_found_count = 0

    for index, row in filtered_df.iterrows():
        title = row['Title']
        print(f"Processing paper {index + 1}/{len(filtered_df)}: {title}")
        citation_data = fetch_paper_citations(title)

        if citation_data["Citation_Count"] is not None or citation_data["Influential_Citation_Count"] is not None:
            updated_rows.append({
                "Title": title,
                "Citation_Count": citation_data["Citation_Count"],
                "Influential_Citation_Count": citation_data["Influential_Citation_Count"]
            })
        else:
            no_paper_found_count += 1

    print(f"No paper found for {no_paper_found_count} papers.")
    return pd.DataFrame(updated_rows)

# Load the CSV file
file_path = 'Paper_Dataset_Bio.csv'
df = pd.read_csv(file_path, encoding='utf-8')

# Filter rows where either 'Citation Count' or 'Influential Citation Count' is NaN
filtered_df = df[(df['Citation_Count'].isna()) | (df['Influential_Citation_Count'].isna())]

# Update citation data
updated_data = update_citation_data(filtered_df)

# Merge the updated data back into the original DataFrame
df.update(updated_data.set_index('Title'))

# Save the updated DataFrame back to CSV
df.to_csv('Paper_Dataset_Bio_Citation_Updated.csv', index=False, encoding='utf-8')


Processing paper 2260/48: Improvement of fully automated airway segmentation on volumetric computed tomographic images using a 2.5 dimensional convolutional neural net
Processing paper 6048/48: Noninvasive imaging of radiolabeled exosome-mimetic nanovesicle using Tc-99m-HMPAO
Processing paper 6107/48: A deep convolutional neural network using directional wavelets for low-dose X-ray CT reconstruction
Rate limit exceeded. Retrying in 5 seconds...
Processing paper 6113/48: Kinetic studies on the formation of various II-VI semiconductor nanocrystals and synthesis of gradient alloy quantum dots emitting in the entire visible range
Processing paper 6115/48: A screening method for beta-glucan hydrolase employing Trypan Blue-coupled beta-glucan agar plate and beta-glucan zymography
Processing paper 6117/48: Transcriptional analysis of the rho-coumarate 3-hydroxylase (C3H) gene from Hibiscus cannabinus L. during developmental stages in various tissues and in response to abiotic stresses
Process

In [23]:
import pandas as pd

# 이미 데이터를 로드한 상태로 가정
file_path = 'Paper_Dataset_Bio_Citation_Updated.csv'  # 새로 업데이트된 데이터를 담고 있는 파일
df = pd.read_csv(file_path, encoding='utf-8')

# 원본 데이터에서 Citation_Count가 NaN인 논문들만 추출
original_file_path = 'Paper_Dataset_Bio.csv'  # 원본 데이터
original_df = pd.read_csv(original_file_path, encoding='utf-8')

# 새로 추가된 데이터는 'Citation_Count'가 NaN에서 값이 채워진 논문들
new_data_df = df[df['Citation_Count'].notna() & original_df['Citation_Count'].isna()]

# 새로 추가된 논문들의 제목을 출력
print("Newly processed papers:")
for title in new_data_df['Title']:
    print(title)


Newly processed papers:
Aqueous Extract of Bambusae Caulis in Taeniam Inhibits PMA-Induced Tumor Cell Invasion and Pulmonary Metastasis: Suppression of NF-kappa B Activation through ROS Signaling
Early neurological outcomes according to CHADS2 score in stroke patients with non-valvular atrial fibrillation
Biotransformation of Fructose to Allose by a One-Pot Reaction Using Flavonifractor plautii D-Allulose 3-Epimerase and Clostridium thermocellum Ribose 5-Phosphate Isomerase
Suppression of lung cancer progression by biocompatible glycerol triacrylate-spermine-mediated delivery of shAkt1
Single-Molecule and Single-Particle-Based Correlation Studies between Localized Surface Plasmons of Dimeric Nanostructures with similar to 1 nm Gap and Surface-Enhanced Raman Scattering
Pupil-size alterations induced by photodisruption during femtosecond laser-assisted cataract surgery
Juxtacrine and paracrine mutual oocytes-granulosa cells interaction: a proposed model
Down-Regulation of Collagen Synthe

In [27]:
import pandas as pd

# 원본 파일과 업데이트된 파일을 로드
original_file_path = 'Paper_Dataset_Bio.csv'
updated_file_path = 'Paper_Dataset_Bio_Citation_Updated.csv'

original_df = pd.read_csv(original_file_path, encoding='utf-8-sig')
updated_df = pd.read_csv(updated_file_path, encoding='utf-8-sig')

# 원본 데이터에서 'Citation_Count'가 NaN인 논문을 찾고, 업데이트된 데이터에서 이들만 가져오기
merged_df = pd.merge(
    original_df[original_df['Citation_Count'].isna()],
    updated_df[['ID', 'Citation_Count', 'Influential_Citation_Count']],
    on='ID',  # ID를 기준으로 병합
    how='left'  # 원본 데이터를 기준으로 병합
)

# merged_df의 컬럼 확인
print("Columns in merged_df:", merged_df.columns)

# 업데이트된 'Citation_Count'와 'Influential_Citation_Count' 값을 원본 데이터에 반영
# column 이름이 다를 경우 확인 후 수정
if 'Citation_Count' in merged_df.columns and 'Influential_Citation_Count' in merged_df.columns:
    original_df.update(merged_df[['ID', 'Citation_Count', 'Influential_Citation_Count']])

# 업데이트된 DataFrame을 새로운 CSV 파일로 저장
output_file = 'Paper_Dataset_Bio_C2.csv'
original_df.to_csv(output_file, index=False, encoding='utf-8-sig')

print(f"Updated data has been saved to {output_file}")


Columns in merged_df: Index(['ID', '과제고유번호', '과제수행년도', '성과발생년도', '성과발생부처명', '성과사업ID', '성과사업명',
       '성과고유번호', '논문_SCI구분_최종', 'Title', 'Journal', 'Journal_Link',
       'Scope_All', 'Scope_Top_Raw', 'Scope_Top', 'Scope_Tree', '논문번호', '논문_권',
       '논문_호', 'DOI', '논문_기여율_확정', 'Affiliation', 'Affiliation_ENG',
       'Affiliation_KR', 'Affiliation_Net', 'Authors', 'Authors_Nom',
       'Citation_Count_x', 'Influential_Citation_Count_x', 'Abstract',
       '육T관련기술', 'Scope_Top_Count', 'Perf_Time', 'GDC_Paper',
       'num_external_tie_paper', 'avg_num_external_tie_paper', 'Authors_Count',
       'Central_1', 'Central_5', 'Central_10', 'Citation_Weighted',
       'Inf_Citation_Weighted', 'Citation_Count_y',
       'Influential_Citation_Count_y'],
      dtype='object')
Updated data has been saved to Paper_Dataset_Bio_C2.csv


In [20]:
import pandas as pd

def save_updated_citations(original_file, updated_data, output_file):
    # Load original dataset
    original_df = pd.read_csv(original_file, encoding='utf-8')

    # Load updated data (already collected)
    updated_df = pd.DataFrame(updated_data)

    # Ensure both DataFrames use the same column name for merging
    if 'Title' not in updated_df.columns:
        raise ValueError("The updated data must include a '논문명' column.")

    # Merge updated data into the original dataset
    # Using '논문명' as the key and updating only 'Citation Count' and 'Influential Citation Count'
    merged_df = original_df.merge(
        updated_df,
        on='Title',
        how='left',  # Keep all original data, add or update from updated data
        suffixes=('', '_updated')
    )

    # Replace missing citation values with the updated ones where applicable
    for col in ['Citation_Count', 'Influential_Citation_Count']:
        if f"{col}_updated" in merged_df.columns:
            merged_df[col] = merged_df[f"{col}_updated"].combine_first(merged_df[col])
            merged_df.drop(columns=[f"{col}_updated"], inplace=True)

    # Save the merged dataset
    merged_df.to_csv(output_file, index=False, encoding='utf-8-sig')
    print(f"Updated dataset saved to: {output_file}")


# 파일 경로 지정
original_file = 'Paper_Dataset_Bio.csv'
output_file = 'Paper_Dataset_Bio_Citation_Updated.csv'

# 함수 호출
save_updated_citations(original_file, updated_data, output_file)


Updated dataset saved to: Paper_Dataset_Bio_Citation_Updated.csv


In [28]:
import pandas as pd

def fill_missing_citation_data(missing_file, updated_file, output_file):
    # Load the datasets
    missing_df = pd.read_csv(missing_file, encoding='utf-8-sig')
    updated_df = pd.read_csv(updated_file, encoding='utf-8-sig')

    # Merge the missing dataset with the updated dataset on 'ID'
    merged_df = missing_df.merge(
        updated_df[['ID', 'Citation_Count', 'Influential_Citation_Count']],
        on='ID',
        how='left'
    )

    # Fill missing Citation_Count and Influential_Citation_Count from the updated dataset
    for col in ['Citation_Count', 'Influential_Citation_Count']:
        merged_df[col] = merged_df[f"{col}_y"].combine_first(merged_df[f"{col}_x"])

    # Drop intermediate columns
    merged_df = merged_df.drop(columns=[f"{col}_x" for col in ['Citation_Count', 'Influential_Citation_Count']] +
                                        [f"{col}_y" for col in ['Citation_Count', 'Influential_Citation_Count']])

    # Save the updated dataset
    merged_df.to_csv(output_file, index=False, encoding='utf-8-sig')
    print(f"Updated dataset saved to: {output_file}")

# Example usage
missing_file = 'Paper_Dataset_Bio_Missing.csv'
updated_file = 'Paper_Dataset_Bio_Citation_Updated.csv'
output_file = 'Paper_Dataset_Bio_Filled.csv'

fill_missing_citation_data(missing_file, updated_file, output_file)


Updated dataset saved to: Paper_Dataset_Bio_Filled.csv


In [29]:
import requests
import pandas as pd
import time

# Replace this with your Semantic Scholar API key
API_KEY = "d9uN8uXwqK2FkU7VYFGJr9ECqcyAYh3Gx0QRyOy7"

# List of paper titles to query
paper_titles = [
    "Kinetic studies on the formation of various II-VI semiconductor nanocrystals and synthesis of gradient alloy quantum dots emitting in the entire visible range",
    "A screening method for β-glucan hydrolase employing Trypan Blue-coupled β-glucan agar plate and β-glucan zymography",
    "Transcriptional analysis of the rho-coumarate 3-hydroxylase (C3H) gene from Hibiscus cannabinus L. during developmental stages in various tissues and in response to abiotic stresses",
    "Toxicity Assessment of SiO2 and TiO2 in Normal Colon Cells, In Vivo and in Human Colon Organoids",
    "Serum-mediated Activation of Bone Marrow–derived Mesenchymal Stem Cells in Ischemic Stroke Patients",
    "Carbon‐Nanotube‐Modified Electrodes for Highly Efficient Acute Neural Recording",
    "Synthesis and biological evaluation of alpha-sulfonamido-N-adamantanecarboxamide derivatives as 11 beta-HSD1 inhibitors",
    "Protective effect of centipedegrass against A beta oligomerization and A beta-mediated cell death in PC12 cells",
    "Development of new Cd-116/Pt target for cyclotron produced Sn-117m as a medical radiometal",
    "Synthesis and Preliminary Evaluation of Ga-68-NOTA-Biphenyl-c(RGDyK) for the Quantification of Integrin (v3)",
    "Head-to-head comparison of C-11-PiB and F-18-FC119S for A beta imaging in healthy subjects, mild cognitive impairment patients, and Alzheimer's disease patients",
    "Bacterial Clearance Is Enhanced by alpha 2,3-and alpha 2,6-Sialyllactose via Receptor-Mediated Endocytosis and Phagocytosis",
    "Crystal structure of GSK3 beta in complex with the flavonoid, morin",
    "Selective regulation of osteoclast adhesion and spreading by PLCγ/PKCα-PKCδ/RhoA-Rac1 signaling",
    "Gliclazide, a KATP channel blocker, inhibits vascular smooth muscle cell proliferation through the CaMKKβ-AMPK pathway",
    "Akinetic mutism following prefrontal injury by an electrical grinder a case report A diffusion tensor tractography study",
    "Complete Genome of Bacillus subtilis subsp. subtilis KCTC 3135T and Variation in Cell Wall Genes of B. subtilis Strains",
    "Triclosan affects axon formation in the neural development stages of zebrafish embryos (Danio rerio)",
    "Auranofin Inhibits RANKL‐Induced Osteoclastogenesis by Suppressing Inhibitors of κB Kinase and Inflammasome‐Mediated Interleukin‐1β Secretion",
    "Association of atopic dermatitis with obesity via a multi-omics approach A protocol for a case-control study",
    "Integrated techno-economic analysis under uncertainty of glycerol steam reforming for H2 production at distributed H2 refueling stations",
    "Efficacy and safety of So-Cheong-Ryong-Tang in patients with atopic dermatitis and respiratory disorders",
    "Acellular dermal matrix combined with oxidized regenerated cellulose for partial breast reconstruction: two case reports",
    "CD226hiCD8+ T Cells Are a Prerequisite for Anti-TIGIT Immunotherapy"
]

# Semantic Scholar API endpoint
BASE_URL = "https://api.semanticscholar.org/graph/v1/paper/search"

# Initialize list for results
results = []

# Function to query the Semantic Scholar API
def fetch_paper_data(title):
    params = {
        "query": title,
        "fields": "title,citationCount,influentialCitationCount",
        "limit": 1  # Fetch the most relevant result
    }
    headers = {"x-api-key": API_KEY}
    response = requests.get(BASE_URL, params=params, headers=headers)
    if response.status_code == 200:
        data = response.json()
        if data.get("data"):
            return data["data"][0]  # Return the first result
        else:
            return None
    else:
        print(f"Failed to fetch data for title: {title} (Status Code: {response.status_code})")
        return None

# Query the API for each paper
for title in paper_titles:
    print(f"Processing: {title}")
    paper_data = fetch_paper_data(title)
    if paper_data:
        results.append({
            "Title": paper_data.get("title", "N/A"),
            "Citation_Count": paper_data.get("citationCount", "N/A"),
            "Influential_Citation_Count": paper_data.get("influentialCitationCount", "N/A")
        })
    else:
        results.append({
            "Title": title,
            "Citation_Count": "N/A",
            "Influential_Citation_Count": "N/A"
        })
    time.sleep(1)  # To avoid hitting the rate limit

# Convert results to a DataFrame
df = pd.DataFrame(results)

# Save to CSV
output_file = "Paper_Citation_Data.csv"
df.to_csv(output_file, index=False, encoding="utf-8")
print(f"Data saved to {output_file}")


Processing: Kinetic studies on the formation of various II-VI semiconductor nanocrystals and synthesis of gradient alloy quantum dots emitting in the entire visible range
Processing: A screening method for β-glucan hydrolase employing Trypan Blue-coupled β-glucan agar plate and β-glucan zymography
Processing: Transcriptional analysis of the rho-coumarate 3-hydroxylase (C3H) gene from Hibiscus cannabinus L. during developmental stages in various tissues and in response to abiotic stresses
Processing: Toxicity Assessment of SiO2 and TiO2 in Normal Colon Cells, In Vivo and in Human Colon Organoids
Processing: Serum-mediated Activation of Bone Marrow–derived Mesenchymal Stem Cells in Ischemic Stroke Patients
Processing: Carbon‐Nanotube‐Modified Electrodes for Highly Efficient Acute Neural Recording
Processing: Synthesis and biological evaluation of alpha-sulfonamido-N-adamantanecarboxamide derivatives as 11 beta-HSD1 inhibitors
Processing: Protective effect of centipedegrass against A beta

#### Journal IF

In [1]:
# Test

import requests
from bs4 import BeautifulSoup

# URL of the journal page
url = 'https://www.scimagojr.com/journalsearch.php?q=13609&tip=sid&clean=0'

# Define the headers to mimic a real browser request
headers = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/93.0.4577.82 Safari/537.36"
}

# Send a GET request to the URL with the headers
response = requests.get(url, headers=headers)

# Check if the request was successful
if response.status_code == 200:
    # Parse the page content with BeautifulSoup
    soup = BeautifulSoup(response.text, 'html.parser')

    # Find the H-index using the specified class
    h_index = soup.find('p', class_='hindexnumber')

    # If the h-index is found, print it, else print an error message
    if h_index:
        print(f"H-index: {h_index.text.strip()}")
    else:
        print("H-index not found.")
else:
    print(f"Failed to retrieve the page. Status code: {response.status_code}")


H-index: 77


In [7]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
import time

# Step 1: Load the dataset and extract unique journal links
file_path = "Paper_Dataset_Bio.csv"  # Update with your actual file path
data = pd.read_csv(file_path)

# Assuming 'Journal_Link' is the column name containing the journal links
unique_journal_links = data['Journal_Link'].dropna().unique()

# Step 2: Define a function to get the H-index from a journal's page
def get_h_index(url):
    headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/93.0.4577.82 Safari/537.36"
    }
    try:
        response = requests.get(url, headers=headers)
        if response.status_code == 200:
            soup = BeautifulSoup(response.text, 'html.parser')
            h_index = soup.find('p', class_='hindexnumber')
            if h_index:
                return h_index.text.strip()
            else:
                return "H-index not found"
        else:
            return f"Failed to retrieve (Status Code: {response.status_code})"
    except Exception as e:
        return f"Error: {e}"

# Step 3: Iterate through the unique journal links and collect H-index values
journal_h_data = []
total_links = len(unique_journal_links)
progress_step = max(total_links // 10, 1)  # Ensure progress_step is at least 1
last_progress_percent = 0

for idx, link in enumerate(unique_journal_links, start=1):
    h_index = get_h_index(link)
    journal_h_data.append({'Journal_Link': link, 'H-index': h_index})

    # Calculate the current progress percentage
    current_progress_percent = (idx / total_links) * 100

    # Provide progress updates only at 10%, 20%, etc.
    if current_progress_percent >= last_progress_percent + 10:
        print(f"Progress: {last_progress_percent + 10}% processed ({idx}/{total_links})")
        last_progress_percent += 10

    time.sleep(2)  # Be polite with the server by adding a delay between requests
    
# Step 4: Save the results to a CSV file
output_file = "Journal_H_List.csv"
output_df = pd.DataFrame(journal_h_data)
output_df.to_csv(output_file, index=False, encoding='utf-8-sig')

print(f"H-index data saved to {output_file}")


Progress: 10% processed (147/1468)
Progress: 20% processed (294/1468)
Progress: 30% processed (441/1468)
Progress: 40% processed (588/1468)
Progress: 50% processed (734/1468)
Progress: 60% processed (881/1468)
Progress: 70% processed (1028/1468)
Progress: 80% processed (1175/1468)
Progress: 90% processed (1322/1468)
Progress: 100% processed (1468/1468)
H-index data saved to Journal_H_List.csv


In [8]:
import pandas as pd

# Step 1: Load the datasets
paper_dataset_file = "Paper_Dataset_Bio.csv"  # Your file path
h_index_file = "Journal_H_List.csv"  # Your file path

paper_data = pd.read_csv(paper_dataset_file)
h_index_data = pd.read_csv(h_index_file)

# Step 2: Merge the datasets on 'Journal_Link'
merged_data = paper_data.merge(h_index_data, on="Journal_Link", how="left")

# Step 3: Save the updated dataset
output_file = "Updated_Paper_Dataset_Bio.csv"
merged_data.to_csv(output_file, index=False, encoding='utf-8-sig')

print(f"Updated dataset saved to {output_file}")


Updated dataset saved to Updated_Paper_Dataset_Bio.csv
